In [2]:
import numpy as np
import mne
import os 
from scipy.io import loadmat
import random

In [3]:
num_channels = 32 

In [4]:
# Creating mne.info object
channel_names_physiological = ['p'+str(x) for x in range(0,8)]
channel_names_eeg = ['Fp1','AF3','F3','F7','FC5','FC1','C3','T7','CP5','CP1','P3','P7','PO3','O1','Oz','Pz','Fp2','AF4','Fz','F4','F8','FC6','FC2','Cz','C4','T8','CP6','CP2','P4','P8','PO4','O2']
channel_names =  channel_names_eeg + channel_names_physiological 

num_channels_eeg = len(channel_names_eeg)
num_channels_physiological = len(channel_names_physiological)

channel_types_eeg= ['eeg' for x in range(num_channels_eeg)]
channel_types_physiological= ['misc' for x in range(num_channels_physiological)]

channel_types =  channel_types_eeg + channel_types_physiological
num_channels = len(channel_names)
sfreq = 128 
info = mne.create_info(channel_names, sfreq, channel_types)

In [5]:
# Define EEG bands
eeg_bands = {'Theta': (4, 8),
             'Alpha': (8, 14),
             'Beta': (14, 31),
             'Gamma': (31, 50)}
list_keys = list(eeg_bands.keys())

In [6]:
tmin = 0.0  # start of each epoch (0ms before the trigger)
tmax = 2  # end of each epoch (2s after the trigger)
baseline = (0, 0)  # means from the first instant to t = 0

In [7]:
def create_model_input_files():
    os.chdir("/home/shreya/DEAP/Data_32subjects/")
    for file in os.listdir():
        print(file)
        content = loadmat(file)
        # separating data and labels in the file 
        data = content['data']
        labels = content['labels']

        
        ## removing the 3 second pre-trial baseline
        eeg_electrodes_data = data[:,:,384:]
        print(eeg_electrodes_data.shape)
        
        file_suffix = file[:-4]

        ## Separating the trials for each subject 
        separating_trials(labels, eeg_electrodes_data, file_suffix)
#         break

In [8]:
def define_events(raw, max_length, dist_bw_events):
    # time point whent event started 
    sample_no_event = np.arange(0, max_length, dist_bw_events).transpose()
    sample_no_event = sample_no_event.reshape(sample_no_event.shape[0],1)
    # duration of event 
    duration_event = np.zeros_like(sample_no_event)
    # type of event 
    int_event_code = duration_event + 1
    events = np.concatenate((sample_no_event , duration_event, int_event_code), axis = 1)
    return events

In [15]:
def save_features(folder1, folder2, feaures_eeg, feaures_p, file_suffix, task_valence, task_arousal):
    for w in range(0,feaures_eeg.shape[0]-5+1):            
        # Task 1
        if task_valence == True:
            n_folder1 = folder1 + "HighValence/"
        elif task_valence == False:
            n_folder1 = folder1 +"LowValence/"
        else:
            n_folder1 = folder1 + "NoneValence/"
            
        filename1 = n_folder1 + file_suffix + "_" + str(w)
        # 5 data points to create one sequence 
        np.savez(filename1,feaures_eeg[w:w+5], feaures_p[w:w+5])
        print("saved file - ", filename1)
        
        # Task 2
        if task_arousal == True:
            n_folder2 = folder2 + "HighArousal/"
        elif task_arousal == False:
            n_folder2 = folder2 + "LowArousal/"
        else:
            n_folder2 = folder2 + "NoneArousal/"
            
        filename2 = n_folder2 + file_suffix + "_" + str(w)
        # 5 data points to create one sequence 
        np.savez(filename2,feaures_eeg[w:w+5], feaures_p[w:w+5])
        print("saved file - ", filename2)
#         break

In [16]:
def psd_features(epochs):
    psds, freqs = mne.time_frequency.psd_welch(epochs, picks =channel_names_eeg , n_per_seg = 256, average='mean')
    
#     print(freqs)
    band_psd = dict()
    ## band wise psd features 
    for band in eeg_bands:  
        ## finding indices for each band
        freq_ix = np.where((freqs >= eeg_bands[band][0]) & (freqs <= eeg_bands[band][1]))[0]
        
        # calculating mean of the log of psd values of the band
        psd_vals = np.log(np.sum(psds[:,:,freq_ix], axis=2))
        psd_vals = psd_vals.reshape((psd_vals.shape[0], psd_vals.shape[1], 1))
        band_psd[band] = psd_vals
    
    #Creating Feature Array
    feature_arr = band_psd[list_keys[0]]
    for i in range(1,len(list_keys)):
        feature_arr = np.concatenate((feature_arr, band_psd[list_keys[i]]), axis=1)
    
    ##  calculating physiological features 
#     print(epochs.pick_channels(channel_names_physiological).get_data().shape)
    p_features = epochs.pick_channels(channel_names_physiological).get_data()
    
    p_var = np.var(p_features, axis=-1)
#     print(p_var.shape)
    
    p_std = np.std(p_features, axis=-1)
#     print(p_std.shape)
    
    p_mean = np.mean(p_features, axis=-1)
#     print(p_mean.shape)
    
    p_max = p_features.max(axis=-1)
#     print(p_max.shape)
    
    p_min = p_features.min(axis=-1)
#     print(p_min.shape)
    
    p_sq_sum = np.square(p_features).sum(axis=-1)
#     print(p_sq_sum.shape)

    
    feature_arr_p = np.concatenate((p_max, p_min, p_mean,p_std, p_var, p_sq_sum), axis=-1)
    # final physiological feature array 
    feature_arr_p = feature_arr_p.reshape(feature_arr_p.shape[0], feature_arr_p.shape[1], 1)
    
    print(feature_arr.shape)
    print(feature_arr_p.shape)
    
    return feature_arr, feature_arr_p

In [17]:
def separating_trials(labels, data, file_suffix):
    for trial_no in range(data.shape[0]):
        print(trial_no)

        ## Creating mne.Raw object 
        raw = mne.io.RawArray(data[trial_no], info)
        raw.load_data()
        
        ## Creating epochs
        events = define_events(raw, 7680, 2*128)
        epochs = mne.Epochs(raw, events, event_id=1, tmin=tmin, tmax=tmax, proj=True, baseline=baseline)
        
        epochs.load_data()
        # Calculating band psd features 
        feature_arr, feature_arr_p = psd_features(epochs)
        
        new_file_suffix = file_suffix + "_" + str(trial_no)
        
        folder1 = "/home/shreya/DEAP/LSTM/TaskValence/"
        folder2 = "/home/shreya/DEAP/LSTM/TaskArousal/"

        #trial x label (valence, arousal, dominance, liking)
        task_valence =  None
        task_arousal = None
        if 1 <= labels[trial_no][0] and labels[trial_no][0] <= 4.8:
            task_valence =  False 
        elif 5.2 <= labels[trial_no][0] and labels[trial_no][0] <= 9:
            task_valence =  True
        else:
            print("not in any range, task_valence")
        
        if 1 <= labels[trial_no][1] and labels[trial_no][1] <= 4.8:
            task_arousal =  False 
        elif 5.2 <= labels[trial_no][1] and labels[trial_no][1] <= 9:
            task_arousal =  True
        else:
            print("not in any range, task_arousal")
        # saving as .npz files 
        save_features(folder1, folder2, feature_arr, feature_arr_p, new_file_suffix, task_valence, task_arousal)
        
#         break

In [18]:
create_model_input_files()

s06.mat
(40, 40, 7680)
0
Creating RawArray with float64 data, n_channels=40, n_times=7680
    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
30 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 30 events and 257 original time points ...
1 bad epochs dropped
Effective window size : 2.000 (s)
(29, 128, 1)
(29, 48, 1)
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_0_0
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_0_0
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_0_1
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_0_1
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_0_2
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_0_2
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_0_3
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_0_3
saved file -  /home/shreya/DEAP/LSTM/TaskVa

    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
30 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 30 events and 257 original time points ...
1 bad epochs dropped
Effective window size : 2.000 (s)
(29, 128, 1)
(29, 48, 1)
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_3_0
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_3_0
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_3_1
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_3_1
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_3_2
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_3_2
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_3_3
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_3_3
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_3_4
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal

saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_7
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_7
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_8
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_8
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_9
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_9
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_10
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_10
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_11
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_11
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_12
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_12
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_5_13
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_5_13
saved file -  /home/shreya/DEAP/L

saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_11
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_11
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_12
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_12
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_13
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_13
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_14
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_14
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_15
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_15
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_16
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_16
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_7_17
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s06_7_17
saved file -  /home/shreya/

saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_17
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_18
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_18
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_19
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_19
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_20
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_20
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_21
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_21
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_22
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_22
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_23
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s06_9_23
saved file -  /home/shreya/DEAP/LSTM/TaskValence/HighValence/s06_9_24
saved file -  /home/

...

saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_30_21
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_30_22
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_30_22
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_30_23
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_30_23
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_30_24
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_30_24
31
Creating RawArray with float64 data, n_channels=40, n_times=7680
    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
30 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 30 events and 257 original time points ...
1 bad epochs dropped
Effective window size : 2.000 (s)
(29, 128, 1)
(29, 48, 1)
not in any range, task_valence
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_31_0
saved file -  /home/sh

    Range : 0 ... 7679 =      0.000 ...    59.992 secs
Ready.
30 matching events found
Applying baseline correction (mode: mean)
Not setting metadata
0 projection items activated
Loading data for 30 events and 257 original time points ...
1 bad epochs dropped
Effective window size : 2.000 (s)
(29, 128, 1)
(29, 48, 1)
not in any range, task_valence
not in any range, task_arousal
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_33_0
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/NoneArousal/s11_33_0
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_33_1
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/NoneArousal/s11_33_1
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_33_2
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/NoneArousal/s11_33_2
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_33_3
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/NoneArousal/s11_33_3
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValenc

saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_4
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_5
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_5
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_6
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_6
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_7
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_7
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_8
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_8
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_9
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_9
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_10
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_35_10
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_35_11
saved file -  /home/shre

saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_9
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_10
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_10
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_11
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_11
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_12
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_12
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_13
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_13
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_14
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_14
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_15
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/HighArousal/s11_37_15
saved file -  /home/shreya/DEAP/LSTM/TaskValence/LowValence/s11_37_16
saved file -  

saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_14
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_15
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_15
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_16
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_16
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_17
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_17
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_18
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_18
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_19
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_19
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_20
saved file -  /home/shreya/DEAP/LSTM/TaskArousal/LowArousal/s11_39_20
saved file -  /home/shreya/DEAP/LSTM/TaskValence/NoneValence/s11_39_21
saved file - 